# Preparing Downloads from Sustainability Disclosure Database

## 1. Download individual report URLs

Prepare output document.

In [1]:
import parameters
import csv

with open(parameters.SDD_urls, 'w') as output:
    writer = csv.writer(output)
    writer.writerow(['year', 'report_url'])

Start webdriver.

In [2]:
from time import sleep
from selenium import webdriver

driver = webdriver.Chrome(parameters.chromedriver_location)
driver.get('http://database.globalreporting.org/search/')
sleep(3)

Adjust search settings of site.

In [3]:
from selenium.webdriver.common.keys import Keys
from selenium.webdriver.common.action_chains import ActionChains

remove_selection = driver.find_element_by_xpath('//*[@class="filter-panel"]//*[@class="btn btn-default"]')
remove_selection.click()
sleep(1)

country_selector = driver.find_element_by_xpath('//*[text()="Country"]/following-sibling::div//*[@type="button"]')
country_selector.click()
sleep(0.5)

canada = driver.find_element_by_xpath('//*[text()="Canada"]')
canada.click()
sleep(0.1)

usa = driver.find_element_by_xpath('//*[text()="United States of America"]')
usa.click()
sleep(0.1)

table_length = driver.find_element_by_name('results-datatable_length')
table_length.click()
actions = ActionChains(driver)
actions.send_keys(Keys.DOWN)
actions.perform()
actions.perform()
actions.perform()
actions.send_keys(Keys.ENTER)
actions.perform()
sleep(3)

Main loop: parse pages and retrieve links to report pages. Save results to csv.

In [4]:
from scrapy.selector import Selector

while True:
    sel = Selector(text=driver.page_source)
    reports = sel.xpath('//*[@class="label label-info"]/..').extract()
    print('Saving results.')
    for report in reports:
        subsel = Selector(text=report)
        url = subsel.xpath('//a/@href').extract_first()
        # Scrapy: would use urljoin... That'd be nice.
        url = 'http://database.globalreporting.org' + url
        year_raw = subsel.xpath('//*[@class="label label-info"]/text()').extract_first()
        year = year_raw.strip()[:-2]

        with open(parameters.SDD_urls, 'a', newline='', encoding='utf-8') as output:
            writer = csv.writer(output)
            writer.writerow([year, url])

    rows = len(driver.find_elements_by_xpath('//*[@role="row"]'))

    if rows == 101:
        next_page = driver.find_element_by_xpath('//*[@id="results-datatable_next"]/a')
        next_page.click()
        print('Found more results.')
        sleep(3)
    else:
        break


Saving results.
Found more results.
Saving results.
Found more results.
Saving results.
Found more results.
Saving results.
Found more results.
Saving results.
Found more results.
Saving results.
Found more results.
Saving results.
Found more results.
Saving results.
Found more results.
Saving results.
Found more results.
Saving results.
Found more results.
Saving results.
Found more results.
Saving results.
Found more results.
Saving results.
Found more results.
Saving results.


## 2. Parse report pages and save links to PDFs.

Make results from csv available.

In [5]:
SDD_urls = []
with open ('SDD_urls.csv') as csvfile:
    reader = csv.reader(csvfile)
    headers = next(reader)
    for row in reader:
        SDD_urls.append({header: row[i] for i, header in enumerate(headers)})

In [6]:
print(SDD_urls)

[{'year': '2014', 'report_url': 'http://database.globalreporting.org/reports/26106/'}, {'year': '2018', 'report_url': 'http://database.globalreporting.org/reports/57385/'}, {'year': '2017', 'report_url': 'http://database.globalreporting.org/reports/47789/'}, {'year': '2016', 'report_url': 'http://database.globalreporting.org/reports/37376/'}, {'year': '2015', 'report_url': 'http://database.globalreporting.org/reports/28447/'}, {'year': '2014', 'report_url': 'http://database.globalreporting.org/reports/21004/'}, {'year': '2013', 'report_url': 'http://database.globalreporting.org/reports/19962/'}, {'year': '2012', 'report_url': 'http://database.globalreporting.org/reports/18483/'}, {'year': '2011', 'report_url': 'http://database.globalreporting.org/reports/8011/'}, {'year': '2009', 'report_url': 'http://database.globalreporting.org/reports/3479/'}, {'year': '2008', 'report_url': 'http://database.globalreporting.org/reports/2360/'}, {'year': '2007', 'report_url': 'http://database.globalre

Prepare second output document.

In [7]:
with open(parameters.SDD_file, 'w') as output:
    writer = csv.writer(output)
    writer.writerow(['company', 
                     'year', 
                     'pdf_url', 
                     'report_type', 
                     'adherence', 
                     'SDG', 
                     'CDP', 
                     'OECD', 
                     'ISO_26000'])

For some of the elements on the website, we have to transform symbols into yes/no.

In [8]:
def transform_symbol(symbol: str):
    if symbol:
        tag = symbol.split('-')[1]
        meaning = '{}'.format('no' if tag=='remove text' else 'yes')
        return meaning
    else:
        return 'no'

In [9]:
transform_symbol('glyphicon glyphicon-remove text-light')

'no'

Prepare scrapy spider.

In [10]:
import scrapy

class SDDReportSpider(scrapy.Spider):
    name = "SDD"
    start_urls = [report['report_url'] for report in SDD_urls]
    
    def parse(self, response):
        sel = Selector(response)
        company = sel.xpath('//*[@id="breadcrumb"]/li[3]/a/text()').extract_first()
        year = sel.xpath('/html/body/div/div/div[2]/div/div[1]/div/ul/li[1]/span[2]/text()').extract_first()
        report_type = sel.xpath('/html/body/div/div/div[2]/div/div[1]/div/ul/li[2]/span[2]/text()').extract_first()
        adherence = sel.xpath('//*[.="Adherence Level:"]/following-sibling::*/text()').extract_first()
        
        SDG_symbol = sel.xpath('//*[.="SDGs:"]/following-sibling::*/@class').extract_first()
        SDG = transform_symbol(SDG_symbol)
        
        CDP_symbol = sel.xpath('//*[.="CDP:"]/following-sibling::*/@class').extract_first()
        CDP = transform_symbol(CDP_symbol)
        
        OECD_symbol = sel.xpath('//*[.="CDP:"]/following-sibling::*/@class').extract_first()
        OECD = transform_symbol(OECD_symbol)
        
        ISO_26000_symbol = sel.xpath('//*[.="ISO 26000:"]/following-sibling::*/@class').extract_first()
        ISO_26000 = transform_symbol(ISO_26000_symbol)
        
        pdf_url = sel.xpath('//*[.=" PDF"]/@href').extract_first()

        if pdf_url:
            yield scrapy.Request(response.urljoin(pdf_url), 
                                 callback=self.parse_pdf, 
                                 meta={'company': company,
                                       'year': year, 
                                       'report_type': report_type,
                                       'adherence': adherence,
                                       'SDG': SDG,
                                       'CDP': CDP,
                                       'OECD': OECD,
                                       'ISO_26000': ISO_26000})
            
    def parse_pdf(self, response):
        company = response.meta['company']
        year = response.meta['year'] 
        report_type = response.meta['report_type']
        adherence = response.meta['adherence']
        SDG = response.meta['SDG']
        CDP = response.meta['CDP']
        OECD = response.meta['OECD']
        ISO_26000 = response.meta['ISO_26000']
        
        sel = Selector(response)
        image_url = sel.xpath('/html/body/div[1]/div/div[1]/img/@src').extract_first()
        pdf_url_raw = image_url.replace('/report-covers/', '/report-pdfs/', 1)
        pdf_url_raw = pdf_url_raw.replace('/profile.jpg?', '.pdf?', 1)
        pdf_url = pdf_url_raw.split('?AWSAccessKeyId')[0]
        
        
        with open(parameters.SDD_file, 'a') as output:
            writer = csv.writer(output)
            writer.writerow([company, 
                             year, 
                             pdf_url, 
                             report_type, 
                             adherence, 
                             SDG, 
                             CDP, 
                             OECD, 
                             ISO_26000])

Run the spider

In [11]:
from scrapy.crawler import CrawlerProcess

process = CrawlerProcess({
    'USER_AGENT': 'Mozilla/4.0 (compatible; MSIE 7.0; Windows NT 5.1)'
    })
process.crawl(SDDReportSpider)

2018-11-17 16:16:15 [scrapy.utils.log] INFO: Scrapy 1.5.1 started (bot: scrapybot)
2018-11-17 16:16:15 [scrapy.utils.log] INFO: Versions: lxml 4.2.5.0, libxml2 2.9.8, cssselect 1.0.3, parsel 1.5.1, w3lib 1.19.0, Twisted 16.2.0, Python 3.6.5 (default, Apr  1 2018, 05:46:30) - [GCC 7.3.0], pyOpenSSL 18.0.0 (OpenSSL 1.1.0i  14 Aug 2018), cryptography 2.3.1, Platform Linux-4.15.0-39-generic-x86_64-with-Ubuntu-18.04-bionic
2018-11-17 16:16:15 [scrapy.crawler] INFO: Overridden settings: {'USER_AGENT': 'Mozilla/4.0 (compatible; MSIE 7.0; Windows NT 5.1)'}
2018-11-17 16:16:15 [scrapy.middleware] INFO: Enabled extensions:
['scrapy.extensions.corestats.CoreStats',
 'scrapy.extensions.memusage.MemoryUsage',
 'scrapy.extensions.logstats.LogStats']
2018-11-17 16:16:15 [scrapy.middleware] INFO: Enabled downloader middlewares:
['scrapy.downloadermiddlewares.httpauth.HttpAuthMiddleware',
 'scrapy.downloadermiddlewares.downloadtimeout.DownloadTimeoutMiddleware',
 'scrapy.downloadermiddlewares.defaulthe

In [12]:
process.start()

2018-11-17 16:16:21 [scrapy.core.engine] DEBUG: Crawled (200) <GET http://database.globalreporting.org/reports/26106/> (referer: None)
2018-11-17 16:16:21 [scrapy.core.engine] DEBUG: Crawled (200) <GET http://database.globalreporting.org/reports/57385/> (referer: None)
2018-11-17 16:16:21 [scrapy.core.engine] DEBUG: Crawled (200) <GET http://database.globalreporting.org/reports/47789/> (referer: None)
2018-11-17 16:16:21 [scrapy.core.engine] DEBUG: Crawled (200) <GET http://database.globalreporting.org/reports/37376/> (referer: None)
2018-11-17 16:16:21 [scrapy.core.engine] DEBUG: Crawled (200) <GET http://database.globalreporting.org/reports/19962/> (referer: None)
2018-11-17 16:16:21 [scrapy.core.engine] DEBUG: Crawled (200) <GET http://database.globalreporting.org/reports/18483/> (referer: None)
2018-11-17 16:16:21 [scrapy.core.engine] DEBUG: Crawled (200) <GET http://database.globalreporting.org/reports/21004/> (referer: None)
2018-11-17 16:16:21 [scrapy.core.engine] DEBUG: Crawled

2018-11-17 16:16:23 [scrapy.core.engine] DEBUG: Crawled (200) <GET http://database.globalreporting.org/reports/10395/> (referer: None)
2018-11-17 16:16:23 [scrapy.core.engine] DEBUG: Crawled (200) <GET http://database.globalreporting.org/reports/5019/> (referer: None)
2018-11-17 16:16:23 [scrapy.core.engine] DEBUG: Crawled (200) <GET http://database.globalreporting.org/reports/6873/> (referer: None)
2018-11-17 16:16:23 [scrapy.core.engine] DEBUG: Crawled (200) <GET http://database.globalreporting.org/reports/41384/> (referer: None)
2018-11-17 16:16:23 [scrapy.core.engine] DEBUG: Crawled (200) <GET http://database.globalreporting.org/reports/43935/download-report-pdf/> (referer: http://database.globalreporting.org/reports/43935/)
2018-11-17 16:16:23 [scrapy.core.engine] DEBUG: Crawled (200) <GET http://database.globalreporting.org/reports/24924/download-report-pdf/> (referer: http://database.globalreporting.org/reports/24924/)
2018-11-17 16:16:23 [scrapy.core.engine] DEBUG: Crawled (200

2018-11-17 16:16:25 [scrapy.core.engine] DEBUG: Crawled (200) <GET http://database.globalreporting.org/reports/60161/> (referer: None)
2018-11-17 16:16:25 [scrapy.core.engine] DEBUG: Crawled (200) <GET http://database.globalreporting.org/reports/51453/> (referer: None)
2018-11-17 16:16:25 [scrapy.core.engine] DEBUG: Crawled (200) <GET http://database.globalreporting.org/reports/21607/download-report-pdf/> (referer: http://database.globalreporting.org/reports/21607/)
2018-11-17 16:16:25 [scrapy.core.engine] DEBUG: Crawled (200) <GET http://database.globalreporting.org/reports/17142/download-report-pdf/> (referer: http://database.globalreporting.org/reports/17142/)
2018-11-17 16:16:25 [scrapy.core.engine] DEBUG: Crawled (200) <GET http://database.globalreporting.org/reports/43905/download-report-pdf/> (referer: http://database.globalreporting.org/reports/43905/)
2018-11-17 16:16:25 [scrapy.core.engine] DEBUG: Crawled (200) <GET http://database.globalreporting.org/reports/58474/download-r

2018-11-17 16:16:27 [scrapy.core.engine] DEBUG: Crawled (200) <GET http://database.globalreporting.org/reports/13398/> (referer: None)
2018-11-17 16:16:27 [scrapy.core.engine] DEBUG: Crawled (200) <GET http://database.globalreporting.org/reports/18502/download-report-pdf/> (referer: http://database.globalreporting.org/reports/18502/)
2018-11-17 16:16:27 [scrapy.core.engine] DEBUG: Crawled (200) <GET http://database.globalreporting.org/reports/20131/> (referer: None)
2018-11-17 16:16:27 [scrapy.core.engine] DEBUG: Crawled (200) <GET http://database.globalreporting.org/reports/13415/download-report-pdf/> (referer: http://database.globalreporting.org/reports/13415/)
2018-11-17 16:16:27 [scrapy.core.engine] DEBUG: Crawled (200) <GET http://database.globalreporting.org/reports/13442/download-report-pdf/> (referer: http://database.globalreporting.org/reports/13442/)
2018-11-17 16:16:27 [scrapy.core.engine] DEBUG: Crawled (200) <GET http://database.globalreporting.org/reports/13431/download-r

2018-11-17 16:16:29 [scrapy.core.engine] DEBUG: Crawled (200) <GET http://database.globalreporting.org/reports/16401/> (referer: None)
2018-11-17 16:16:29 [scrapy.core.engine] DEBUG: Crawled (200) <GET http://database.globalreporting.org/reports/39451/download-report-pdf/> (referer: http://database.globalreporting.org/reports/39451/)
2018-11-17 16:16:29 [scrapy.core.engine] DEBUG: Crawled (200) <GET http://database.globalreporting.org/reports/22244/download-report-pdf/> (referer: http://database.globalreporting.org/reports/22244/)
2018-11-17 16:16:29 [scrapy.core.engine] DEBUG: Crawled (200) <GET http://database.globalreporting.org/reports/31038/download-report-pdf/> (referer: http://database.globalreporting.org/reports/31038/)
2018-11-17 16:16:29 [scrapy.core.engine] DEBUG: Crawled (200) <GET http://database.globalreporting.org/reports/46302/download-report-pdf/> (referer: http://database.globalreporting.org/reports/46302/)
2018-11-17 16:16:29 [scrapy.core.engine] DEBUG: Crawled (200)

...

2018-11-17 16:22:21 [scrapy.core.engine] DEBUG: Crawled (200) <GET http://database.globalreporting.org/reports/2345/download-report-pdf/> (referer: http://database.globalreporting.org/reports/2345/)
2018-11-17 16:22:21 [scrapy.core.engine] DEBUG: Crawled (200) <GET http://database.globalreporting.org/reports/26114/> (referer: None)
2018-11-17 16:22:21 [scrapy.core.engine] DEBUG: Crawled (200) <GET http://database.globalreporting.org/reports/10429/> (referer: None)
2018-11-17 16:22:21 [scrapy.core.engine] DEBUG: Crawled (200) <GET http://database.globalreporting.org/reports/22170/> (referer: None)
2018-11-17 16:22:21 [scrapy.core.engine] DEBUG: Crawled (200) <GET http://database.globalreporting.org/reports/6814/> (referer: None)
2018-11-17 16:22:22 [scrapy.core.engine] DEBUG: Crawled (200) <GET http://database.globalreporting.org/reports/41901/> (referer: None)
2018-11-17 16:22:22 [scrapy.core.engine] DEBUG: Crawled (200) <GET http://database.globalreporting.org/reports/58718/download-r

2018-11-17 16:22:23 [scrapy.core.engine] DEBUG: Crawled (200) <GET http://database.globalreporting.org/reports/17144/download-report-pdf/> (referer: http://database.globalreporting.org/reports/17144/)
2018-11-17 16:22:23 [scrapy.core.engine] DEBUG: Crawled (200) <GET http://database.globalreporting.org/reports/6824/download-report-pdf/> (referer: http://database.globalreporting.org/reports/6824/)
2018-11-17 16:22:23 [scrapy.core.engine] DEBUG: Crawled (200) <GET http://database.globalreporting.org/reports/316/> (referer: None)
2018-11-17 16:22:23 [scrapy.core.engine] DEBUG: Crawled (200) <GET http://database.globalreporting.org/reports/17156/download-report-pdf/> (referer: http://database.globalreporting.org/reports/17156/)
2018-11-17 16:22:24 [scrapy.core.engine] DEBUG: Crawled (200) <GET http://database.globalreporting.org/reports/1640/download-report-pdf/> (referer: http://database.globalreporting.org/reports/1640/)
2018-11-17 16:22:24 [scrapy.core.engine] DEBUG: Crawled (200) <GET 

2018-11-17 16:22:25 [scrapy.core.engine] DEBUG: Crawled (200) <GET http://database.globalreporting.org/reports/48809/download-report-pdf/> (referer: http://database.globalreporting.org/reports/48809/)
2018-11-17 16:22:25 [scrapy.core.engine] DEBUG: Crawled (200) <GET http://database.globalreporting.org/reports/37664/> (referer: None)
2018-11-17 16:22:25 [scrapy.core.engine] DEBUG: Crawled (200) <GET http://database.globalreporting.org/reports/37663/> (referer: None)
2018-11-17 16:22:25 [scrapy.core.engine] DEBUG: Crawled (200) <GET http://database.globalreporting.org/reports/37654/> (referer: None)
2018-11-17 16:22:25 [scrapy.core.engine] DEBUG: Crawled (200) <GET http://database.globalreporting.org/reports/37659/> (referer: None)
2018-11-17 16:22:25 [scrapy.core.engine] DEBUG: Crawled (200) <GET http://database.globalreporting.org/reports/2353/> (referer: None)
2018-11-17 16:22:26 [scrapy.core.engine] DEBUG: Crawled (200) <GET http://database.globalreporting.org/reports/4976/> (refere

2018-11-17 16:22:27 [scrapy.core.engine] DEBUG: Crawled (200) <GET http://database.globalreporting.org/reports/6834/> (referer: None)
2018-11-17 16:22:27 [scrapy.core.engine] DEBUG: Crawled (200) <GET http://database.globalreporting.org/reports/9688/download-report-pdf/> (referer: http://database.globalreporting.org/reports/9688/)
2018-11-17 16:22:27 [scrapy.core.engine] DEBUG: Crawled (200) <GET http://database.globalreporting.org/reports/42938/> (referer: None)
2018-11-17 16:22:27 [scrapy.core.engine] DEBUG: Crawled (200) <GET http://database.globalreporting.org/reports/4979/> (referer: None)
2018-11-17 16:22:27 [scrapy.core.engine] DEBUG: Crawled (200) <GET http://database.globalreporting.org/reports/3470/> (referer: None)
2018-11-17 16:22:27 [scrapy.core.engine] DEBUG: Crawled (200) <GET http://database.globalreporting.org/reports/35772/> (referer: None)
2018-11-17 16:22:28 [scrapy.core.engine] DEBUG: Crawled (200) <GET http://database.globalreporting.org/reports/11106/> (referer: 

2018-11-17 16:22:29 [scrapy.core.engine] DEBUG: Crawled (200) <GET http://database.globalreporting.org/reports/22490/download-report-pdf/> (referer: http://database.globalreporting.org/reports/22490/)
2018-11-17 16:22:29 [scrapy.core.engine] DEBUG: Crawled (200) <GET http://database.globalreporting.org/reports/35893/> (referer: None)
2018-11-17 16:22:29 [scrapy.core.engine] DEBUG: Crawled (200) <GET http://database.globalreporting.org/reports/26110/> (referer: None)
2018-11-17 16:22:29 [scrapy.core.engine] DEBUG: Crawled (200) <GET http://database.globalreporting.org/reports/15590/> (referer: None)
2018-11-17 16:22:29 [scrapy.core.engine] DEBUG: Crawled (200) <GET http://database.globalreporting.org/reports/17163/download-report-pdf/> (referer: http://database.globalreporting.org/reports/17163/)
2018-11-17 16:22:29 [scrapy.core.engine] DEBUG: Crawled (200) <GET http://database.globalreporting.org/reports/7656/> (referer: None)
2018-11-17 16:22:30 [scrapy.core.engine] DEBUG: Crawled (20

In [13]:
process.stop()

<DeferredList at 0x7fd5e2a08940 current result: []>

## 2. Download pdfs

Load results from previous step.

In [14]:
SDD_pdfs = []
with open ('SDD.csv') as csvfile:
    reader = csv.reader(csvfile)
    headers = next(reader)
    for row in reader:
        SDD_pdfs.append({header: row[i] for i, header in enumerate(headers)})

In [15]:
print(SDD_pdfs)

[{'company': '3M', 'year': '2017', 'pdf_url': 'https://sdd-pdf.s3.amazonaws.com/report-pdfs/2017/02c3a7a5b905b54987ab6367c98c4745.pdf', 'report_type': 'GRI - G4', 'adherence': 'In accordance - Core', 'SDG': 'yes', 'CDP': 'yes', 'OECD': 'yes', 'ISO_26000': 'no'}, {'company': '3M', 'year': '2016', 'pdf_url': 'https://sdd-pdf.s3.amazonaws.com/report-pdfs/2016/cb871d13ec684683dbe3071802cddb7f.pdf', 'report_type': 'GRI - G4', 'adherence': 'In accordance - Core', 'SDG': 'yes', 'CDP': 'yes', 'OECD': 'yes', 'ISO_26000': 'no'}, {'company': '3M', 'year': '2013', 'pdf_url': 'https://sdd-pdf.s3.amazonaws.com/report-pdfs/2013/239cf41377c9698669cb2e9a26e0da46.pdf', 'report_type': 'GRI - G3.1', 'adherence': 'C+', 'SDG': 'no', 'CDP': 'yes', 'OECD': 'yes', 'ISO_26000': 'no'}, {'company': '3M', 'year': '2015', 'pdf_url': 'https://sdd-pdf.s3.amazonaws.com/report-pdfs/2015/c9329ce82a2ec4c578dab0aa1ccc37f0.pdf', 'report_type': 'GRI - G4', 'adherence': 'In accordance - Core', 'SDG': 'no', 'CDP': 'no', 'OECD

Create folder for PDFs.

In [16]:
from os import makedirs
try:
    makedirs(parameters.SDD_folder)
except FileExistsError:
    print('Saving to existing folder.')

Saving to existing folder.


Adjust company names for writing to file names.

In [17]:
for row in SDD_pdfs:
    row['company'] = row['company'].replace(',', '')
    row['company'] = row['company'].replace('.', '')
    row['company'] = row['company'].replace('/', '-')

In [18]:
print(SDD_pdfs)

[{'company': '3M', 'year': '2017', 'pdf_url': 'https://sdd-pdf.s3.amazonaws.com/report-pdfs/2017/02c3a7a5b905b54987ab6367c98c4745.pdf', 'report_type': 'GRI - G4', 'adherence': 'In accordance - Core', 'SDG': 'yes', 'CDP': 'yes', 'OECD': 'yes', 'ISO_26000': 'no'}, {'company': '3M', 'year': '2016', 'pdf_url': 'https://sdd-pdf.s3.amazonaws.com/report-pdfs/2016/cb871d13ec684683dbe3071802cddb7f.pdf', 'report_type': 'GRI - G4', 'adherence': 'In accordance - Core', 'SDG': 'yes', 'CDP': 'yes', 'OECD': 'yes', 'ISO_26000': 'no'}, {'company': '3M', 'year': '2013', 'pdf_url': 'https://sdd-pdf.s3.amazonaws.com/report-pdfs/2013/239cf41377c9698669cb2e9a26e0da46.pdf', 'report_type': 'GRI - G3.1', 'adherence': 'C+', 'SDG': 'no', 'CDP': 'yes', 'OECD': 'yes', 'ISO_26000': 'no'}, {'company': '3M', 'year': '2015', 'pdf_url': 'https://sdd-pdf.s3.amazonaws.com/report-pdfs/2015/c9329ce82a2ec4c578dab0aa1ccc37f0.pdf', 'report_type': 'GRI - G4', 'adherence': 'In accordance - Core', 'SDG': 'no', 'CDP': 'no', 'OECD

Save results back to csv.

In [19]:
with open(parameters.SDD_file, 'w') as output:
    writer = csv.writer(output)
    writer.writerow(['company', 'year', 'pdf_url', 'report_type', 'adherence', 'SDG', 'CDP', 'OECD', 'ISO_26000'])
    for row in SDD_pdfs:
        writer.writerow([row['company'],
                        row['year'],
                        row['pdf_url'],
                        row['report_type'],
                        row['adherence'],
                        row['SDG'],
                        row['CDP'],
                        row['OECD'],
                        row['ISO_26000']])

Download pdfs to folder.

In [25]:
from urllib.request import urlretrieve
from urllib.error import HTTPError

for row in SDD_pdfs:
    if row['pdf_url']:
        file_name = '{}/{},{}'.format(parameters.SDD_folder, row['company'], row['year'])
        try:
            urlretrieve(row['pdf_url'], file_name)
        except HTTPError:
            print('PDF for {}, year {} at {} not found.'.format(row['company'], 
                                                                row['year'], 
                                                                row['pdf_url']))
            pass

PDF for American Express, year 2011 at https://sdd-pdf.s3.amazonaws.com/report-pdfs/2011/65af2286b0a78453d2b8f43eb18ce82f.pdf not found.
PDF for ArcelorMittal USA, year 2016 at https://sdd-pdf.s3.amazonaws.com/report-pdfs/2016/75395f9397c4ffbfc4c58c3979acd291.pdf not found.
PDF for Arrow Electronics, year 2016 at https://sdd-pdf.s3.amazonaws.com/report-pdfs/2016/d473661f9eeeb73c28d2e2a089989377.pdf not found.
PDF for Avalon Advanced Materials, year 2015 at https://sdd-pdf.s3.amazonaws.com/report-pdfs/2015/91a48e681b3503bf7b1dbbffca7d04af.pdf not found.
PDF for Bombardier Recreational Products, year 2016 at https://sdd-pdf.s3.amazonaws.com/report-pdfs/2016/580855923b15d939b37ddb0dde447ab5.pdf not found.
PDF for Canadian Pacific Railway (CPR), year 2012 at https://sdd-pdf.s3.amazonaws.com/report-pdfs/2012/9cf27f5ff6fbdd43aae19a6929f293ad.pdf not found.
PDF for Canadian Pacific Railway (CPR), year 2013 at https://sdd-pdf.s3.amazonaws.com/report-pdfs/2013/b27f8f67cca42fccece60320c4fb8210.p

## 3. Read pdfs into text

We read the pdfs into a text file first, so that we can free up some space.

In [1]:
import parameters
from os import listdir
pdfs = listdir(parameters.SDD_folder)
print(pdfs[:5])

['Republic Services Inc,2017', 'Hydro Québec,2009', 'Walmart Canada,2013', 'American Chemical Society,2013', 'J+J Flooring Group,2017']


In [2]:
reports = []
for pdf in pdfs:
    reports.append({'company': pdf.split(',')[0], 'year': pdf.split(',')[1], 'file': pdf})
reports[:5]

[{'company': 'Republic Services Inc',
  'year': '2017',
  'file': 'Republic Services Inc,2017'},
 {'company': 'Hydro Québec', 'year': '2009', 'file': 'Hydro Québec,2009'},
 {'company': 'Walmart Canada', 'year': '2013', 'file': 'Walmart Canada,2013'},
 {'company': 'American Chemical Society',
  'year': '2013',
  'file': 'American Chemical Society,2013'},
 {'company': 'J+J Flooring Group',
  'year': '2017',
  'file': 'J+J Flooring Group,2017'}]

We run an Appache Tika server in to handle the conversion of the PDFs to text (https://tika.apache.org/). The parser command sends the file names to the Tika server and receives the extracted text.

In [3]:
from tika import parser

for report in reports:
    try:
        report['content'] = parser.from_file(parameters.SDD_folder + '/' + report['file'], 'http://0.0.0.0:9998/')['content']
    except UnicodeEncodeError:
        print('Unrecognized character in {}. Skipping.'.format(report['file']))
        report['content'] = ''
reports[:5]

Unrecognized character in Hartsfield‐Jackson Atlanta International Airport,2012. Skipping.


[{'company': 'Republic Services Inc',
  'year': '2017',
  'file': 'Republic Services Inc,2017',
  'content': '\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\nSustainability Report\n\n2016\n\n\n\nThis Sustainability Report reflects our \nwork in Republic’s five elements of \nsustainability: Operations, Materials \nManagement, Communities, Safety \nand People.\n\nThis Report reflects year-end 2016 results,  \nunless otherwise noted.\n\nTable of Contents\n3 Our Blue Planet™\n\n4 Message from Don Slager\n\n6 Our Company\n\n8 Leading the Way\n\n10 Our Sustainability Goals\n\n12 Operations\n\n22 Materials Management\n\n34 Communities\n\n40 Safety\n\n46 People\n\n52 Appendix\n\n3\n\nWe believe in the preservation of a Blue Planet...a cleaner, safer and healthier world where people thrive – not just for today, but for \n\ngenerations to come.\n\nWe are guardians of our environment and have a responsibility to regenerate our planet with the materials 

Finally, write results to csv.

In [6]:
import csv
import parameters

with open(parameters.SDD_file, 'w') as output:
    writer = csv.writer(output)
    writer.writerow(['company', 'year', 'file', 'content'])
    for row in reports:
        writer.writerow([row['company'],
                        row['year'],
                        row['file'],
                        row['content']])